In [1]:
import xarray as xr, numpy as np
from skimage.transform import resize, rescale
import pathlib, yaml
from joblib import Parallel, delayed

In [2]:
with open('../input.yml') as f:
    input_data = yaml.load(f, Loader=yaml.loader.SafeLoader)

In [3]:
study_area = input_data['study_area']
lat_south = input_data['study_area_bounds']['lat_south']
lat_north = input_data['study_area_bounds']['lat_north']
lon_west = input_data['study_area_bounds']['lon_west']
lon_east = input_data['study_area_bounds']['lon_east']

year_range = sorted(list(range(input_data['training_period']['start'], input_data['training_period']['end']+1)) + \
                    list(range(input_data['validation_period']['start'], input_data['validation_period']['end']+1)) + \
                    list(range(input_data['testing_period']['start'], input_data['testing_period']['end']+1)))

out_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'orographic_rainfall')
out_dir.mkdir(parents=True, exist_ok=True)

in_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'orographic_rainfall')
in_extra_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'input_data_extra')

In [4]:
tp = xr.open_dataset(in_extra_dir/'era5_large_scale_rainfall.nc')
tp_hr_extra = xr.open_dataset(in_extra_dir/'era5_land_rainfall.nc')
rain_topo = xr.open_dataset(in_dir/'era5_orographic_rainfall.nc')
wind_lat = tp_hr_extra.lat.sel(lat=slice(lat_north, lat_south)).values
wind_lon = tp_hr_extra.lon.sel(lon=slice(lon_west, lon_east)).values

In [5]:
def interp_rain(lr, hr_lat, hr_lon):
    hr = lr.interp(lat=hr_lat, lon=hr_lon, method="cubic")
    return hr

tpi = np.array(Parallel(n_jobs=30)(delayed(interp_rain)(tpt, wind_lat, wind_lon) for tpt in tp.rainfall))

In [6]:
sr_ph = tpi + rain_topo.rainfall.values
sr_ph[sr_ph<0] = 0

In [7]:
with xr.open_dataset(in_dir/'era5_orographic_rainfall.nc') as ds1:

    ds = xr.Dataset(
        data_vars=dict(rainfall=(["time", "lon", "lat"], np.squeeze(sr_ph))),
        coords=dict(lon=ds1.lon.data, lat=ds1.lat.data, time=ds1.time),
        attrs=dict(description="ERA5 daily rainfall downscaled with Upslope Method"),
    )

    ds.to_netcdf(out_dir/"era5_sr1.nc")